# ___Project - Milestone 1___

###  <span style="color: gray;">Jade Chen, Sam Thorne, Dia Zavery</span> 

#### Dataset Background Information

Athlete non-athlete survey data can be found on [figshare.com](https://figshare.com/articles/dataset/Athlete_Non-Athlete_MH_Survey_-_ALL_DATA_csv/13035050)

Data collected from a mental health survey on 753 individuals. Data contains demographic information, general health and lifestyle information, athlete information, Mental health and answers to mental health related questions. This study was completed in early 2020 and questioned how individuals mental health was coping in the early stages of the COVID-19 pandemic.

# PART I: Initial Exploration

### Set Up

In [1]:
import pandas as pd
import numpy as np
import altair as alt

# Suppress FutureWarning
import warnings
warnings.filterwarnings("ignore")

### Read in Data

First we check the character type, then we read in information with proper encoding.

In [2]:
#Check character type
import chardet

with open('data/Athlete_Non-Athlete.csv', 'rb') as rawdata:
    result = chardet.detect(rawdata.read(10000))
result

{'encoding': 'ascii', 'confidence': 1.0, 'language': ''}

In [3]:
#Used more robust encoding 'ISO-8859-1' instead of 'ascii' (got error)
data = pd.read_csv('data/Athlete_Non-Athlete.csv', encoding='ISO-8859-1')
data.head(5)

Respondent ID  Gender:  Age Group:  Country During Lockdown  \
0    11785667914        2           2                        2   
1    11785634332        2           3                        1   
2    11784520014        2           3                        2   
3    11783867710        2           1                        2   
4    11783726076        2           1                        2   

  Mental Health Condition?    Occupation:  Marital Status:  Smoking Status:  \
0                      999     Unemployed                1                1   
1                  3, 5, 6  Administrator                2                1   
2                      999        Finance                1                3   
3                        2     Unemployed                1                1   
4                      999        Student                1                1   

   Five Fruit and Veg  Hours sleep:  ... LONE_ TOTAL  LONE_ Emotional  \
0                   2           6.5  ...        3.67             4.33   
1                   1           7.0  ...        4.33             4.00   
2                   2           4.0  ...        3.50             4.33   
3                   2           8.0  ...        2.67             3.00   
4                   1           8.5  ...        4.33             5.00   

  LONE_ Social  I experience a general sense of emptiness  \
0         3.00                                          4   
1         4.67                                          5   
2         2.67                                          4   
3         2.33                                          4   
4         3.67                                          5   

   I miss having people around  There are many people I can trust completely*  \
0                            5                                              4   
1                            2                                              4   
2                            4                                              4   
3                            3                                              2   
4                            5                                              5   

   I often feel rejected  There are enough people I feel close to*  \
0                      4                                         2   
1                      5                                         5   
2                      5                                         2   
3                      2                                         1   
4                      5                                         4   

   There are plenty of people I can rely on when I have problems*  Unnamed: 84  
0                                                  3                       NaN  
1                                                  5                       NaN  
2                                                  2                       NaN  
3                                                  4                       NaN  
4                                                  2                       NaN  

[5 rows x 85 columns]

### Data Cleaning
Drop the last column with no values (empty).

In [4]:
data = data.drop(data.columns[84], axis=1)
data.head(5)

Respondent ID  Gender:  Age Group:  Country During Lockdown  \
0    11785667914        2           2                        2   
1    11785634332        2           3                        1   
2    11784520014        2           3                        2   
3    11783867710        2           1                        2   
4    11783726076        2           1                        2   

  Mental Health Condition?    Occupation:  Marital Status:  Smoking Status:  \
0                      999     Unemployed                1                1   
1                  3, 5, 6  Administrator                2                1   
2                      999        Finance                1                3   
3                        2     Unemployed                1                1   
4                      999        Student                1                1   

   Five Fruit and Veg  Hours sleep:  ...  \
0                   2           6.5  ...   
1                   1           7.0  ...   
2                   2           4.0  ...   
3                   2           8.0  ...   
4                   1           8.5  ...   

  I tend to take a long time to get over setbacks in my life*  LONE_ TOTAL  \
0                                                  2                  3.67   
1                                                  1                  4.33   
2                                                  3                  3.50   
3                                                  4                  2.67   
4                                                  5                  4.33   

  LONE_ Emotional  LONE_ Social  I experience a general sense of emptiness  \
0            4.33          3.00                                          4   
1            4.00          4.67                                          5   
2            4.33          2.67                                          4   
3            3.00          2.33                                          4   
4            5.00          3.67                                          5   

   I miss having people around  There are many people I can trust completely*  \
0                            5                                              4   
1                            2                                              4   
2                            4                                              4   
3                            3                                              2   
4                            5                                              5   

   I often feel rejected  There are enough people I feel close to*  \
0                      4                                         2   
1                      5                                         5   
2                      5                                         2   
3                      2                                         1   
4                      5                                         4   

   There are plenty of people I can rely on when I have problems*  
0                                                  3               
1                                                  5               
2                                                  2               
3                                                  4               
4                                                  2               

[5 rows x 84 columns]

### Data Wrangling
First, we remove the colons (`:`) and question marks (`?`) in the column names.

Second, we transform the column data types to appropriate data types for ease of finding cardinality.

Lastly, we change cells with the values of `999` to `NaN`, because we assume that it means 'prefer not to answer'.

In [5]:
data.columns = data.columns.str.replace(r'[?:]$', '', regex=True)

In [6]:
categorical = ['Respondent ID', 'Gender', 'Age Group', 'Country During Lockdown', 'Mental Health Condition', 'Occupation', 'Marital Status', 'Smoking Status', 'Five Fruit and Veg', 'Shielded', '# in lockdown bubble', 'Athlete/Non-Athlete', 'What sport do you play', 'Individual/Team athlete']

for column_name in categorical:
    data[column_name] = data[column_name].astype('category')

temporal = ['Survey Date']

for column_name in temporal:
    data[column_name] = pd.to_datetime(data[column_name])

In [7]:
data.replace(999, np.nan, inplace=True)

## Data Attribute Information: Type, Cardinality, and Missing Values
The following dataframe gives the name, data type, cardinality (unique values for categorical features, and range for quantitative and temporal features), and missing values of each attribute.

In [8]:
pd.set_option('display.max_rows', None)
# Function to determine if a column is quantitative
def is_quantitative(column):
    return pd.api.types.is_numeric_dtype(column)

quant_range = []

# Loop through the columns of the original DataFrame
for column_name in data.columns:
    column_data = data[column_name]
    data_type = column_data.dtype
    if is_quantitative(column_data):
        data_range = f'{column_data.min()} - {column_data.max()}'
        unique_values = column_data.nunique() #TEMP
        #unique_values = 'N/A'
    else:
        data_range = 'N/A'
        unique_values = column_data.nunique()
        
    count_na = data[column_name].isna().sum()
    quant_range.append({'Column': column_name, 'Data Type': data_type, 'Unique Values': unique_values, 'Range': data_range, 'Missing Values': count_na})

# Convert the list of dictionaries to a DataFrame
quant_range_df = pd.DataFrame(quant_range)

# Display the DataFrame with data types and ranges
quant_range_df

Column       Data Type  \
0                                       Respondent ID        category   
1                                              Gender        category   
2                                           Age Group        category   
3                             Country During Lockdown        category   
4                             Mental Health Condition        category   
5                                          Occupation        category   
6                                      Marital Status        category   
7                                      Smoking Status        category   
8                                  Five Fruit and Veg        category   
9                                         Hours sleep         float64   
10                                        Survey Date  datetime64[ns]   
11                                           Shielded        category   
12                                    Dates Shielding          object   
13                            Weeks Social Distancing           int64   
14                               # in lockdown bubble        category   
15                                Athlete/Non-Athlete        category   
16                                        AIMS_ TOTAL         float64   
17                                    Social Identity         float64   
18                       I consider myself an athlete         float64   
19                 I have many goals related to sport         float64   
20                    most of my friends are athletes         float64   
21                                        Exclusivity         float64   
22        Sport is the most important part of my life         float64   
23  I spend more time thinking about sport than an...         float64   
24                               Negative Affectivity         float64   
25   I feel bad about myself when I do badly in sport         float64   
26  I would be very depressed if I were injured an...         float64   
27                             What sport do you play        category   
28                                        Sport level         float64   
29                         Total weekly playing hours         float64   
30                              Weekly training hours         float64   
31                             Weekly competing hours         float64   
32                            Individual/Team athlete        category   
33                                     MHC-SF OVERALL         float64   
34                                Emotional Wellbeing         float64   
35                                              Happy         float64   
36                                 Interested in life         float64   
37                                          Satisfied         float64   
38                                   Social Wellbeing         float64   
39  That you had something important to contribute...         float64   
40  That you belonged to a community (like a socia...         float64   
41  That our society is becoming a better place fo...         float64   
42                     That people are basically good         float64   
43  That the way our society works makes sense to you         float64   
44                            Psychological Wellbeing         float64   
45      That you liked most parts of your personality         float64   
46  Good at managing the responsibilities of your ...         float64   
47  That you had warm and trusting relationships w...         float64   
48  That you had experiences that challenged you t...         float64   
49  Confident to think or express your own ideas a...         float64   
50  That your life has a sense of direction or mea...         float64   
51                                       HADS OVERALL         float64   
52                                     HADS-A AVERAGE         float64   
53                                     HADS-D AVERAGE         float64   
54                         I fee

In [9]:
#pd.reset_option('display.max_rows')

### Levels of Categorical Variables
Specifically, if the categorical variable has less than 10 levels, we can see the count of each level.

In [ ]:
#Referenced from DSCI 320 Prog4
def cat_cardinality():
    for field in categorical:
        print(field, " ", data[field].nunique())
        if data[field].nunique() < 10:
            print(data[field].value_counts())

cat_cardinality()

### Semantics
TODO

### Insights

TODO

### Potential Challenges

TODO

## Exploratory Data Analysis

### Size of the Dataset
As we can see below, there are 753 rows and 84 columns.

In [12]:
data.shape

(753, 84)

### Numeric Summaries - Frequency Table (Categorical)

For all the categorical features, we have created a frequency table to show the distribution of values.

In [48]:
# Get a list of categorical columns (excluding 'Respondent ID')
categorical_columns = [col for col in data.select_dtypes(include=['category']).columns if col != "Respondent ID"]

# Create frequency tables for each categorical column
frequency_tables = {}
for column in categorical_columns:
    frequency_table = data[column].value_counts()
    frequency_tables[column] = frequency_table

# Display the frequency tables
for column, table in frequency_tables.items():
    print(table)
    print("\n")


Gender
2    400
1    353
Name: count, dtype: int64


Age Group
2    203
3    182
4    159
1     73
5     73
6     48
7     15
Name: count, dtype: int64


Country During Lockdown
1    558
2    186
4      4
3      2
5      1
6      1
7      1
Name: count, dtype: int64


Mental Health Condition
2          578
999         98
6           21
8           21
3, 6        15
3           12
5            2
7            2
3, 5, 6      1
3, 6, 7      1
4            1
6, 6         1
Name: count, dtype: int64


Occupation
Student                                                   83
Teacher                                                   46
Retired                                                   38
Civil servant                                             16
Lecturer                                                  13
Civil Servant                                             12
Accountant                                                10
Manager                                                    9


### Numeric Summaries - Frequency Table (Numerical)

For all the numerical features, we have created a frequency table to show the distribution of values.

In [50]:
numeric_columns_all = data.select_dtypes(include=['number']).columns.tolist()

# Create frequency tables for each categorical column
frequency_tables = {}
for column in numeric_columns_all:
    frequency_table = data[column].value_counts()
    frequency_tables[column] = frequency_table

# Display the frequency tables
for column, table in frequency_tables.items():
    print(table)
    print("\n")


Hours sleep
7.0     191
8.0     146
7.5     137
6.5      74
6.0      74
8.5      43
5.0      24
5.5      19
9.0      19
9.5       7
4.5       6
4.0       5
10.0      2
10.5      2
3.5       1
2.0       1
3.0       1
1.5       1
Name: count, dtype: int64


Weeks Social Distancing
5    319
4    174
6    106
7     67
3     49
2     20
0     14
1      4
Name: count, dtype: int64


AIMS_ TOTAL
5.14    33
6.14    32
5.43    31
5.29    26
6.00    26
5.86    26
5.57    25
5.00    25
6.29    24
4.86    23
4.57    20
5.71    18
4.43    17
4.14    16
4.71    15
3.86    14
4.29    13
6.43    12
4.00    11
3.71    10
6.57    10
6.71     9
2.86     9
6.86     8
7.00     8
1.00     7
3.29     6
1.43     5
1.14     4
2.14     4
3.57     4
3.43     3
3.14     3
2.71     3
1.29     3
2.00     3
2.43     3
3.00     2
1.86     2
2.57     2
2.29     1
1.57     1
1.71     1
Name: count, dtype: int64


Social Identity
6.33    66
5.67    65
6.00    56
5.33    46
5.00    44
6.67    39
4.67    38
7.00    28
4.3

### Numeric Summaries - Summary Statistics (Numerical)

Here we have generated summary statistitcs for all numerical columns.

In [56]:
data[numeric_columns_all].describe()

Hours sleep  Weeks Social Distancing  AIMS_ TOTAL  Social Identity  I consider myself an athlete  I have many goals related to sport  most of my friends are athletes  Exclusivity  Sport is the most important part of my life  I spend more time thinking about sport than anything else  Negative Affectivity  I feel bad about myself when I do badly in sport  I would be very depressed if I were injured and could not compete in sport  Sport level  Total weekly playing hours  Weekly training hours  Weekly competing hours  MHC-SF OVERALL  Emotional Wellbeing   Happy  Interested in life  Satisfied  Social Wellbeing  That you had something important to contribute to society  That you belonged to a community (like a social group or your neighbourhood)  That our society is becoming a better place for people like you  That people are basically good  That the way our society works makes sense to you  Psychological Wellbeing  That you liked most parts of your personality  Good at managing the responsibilities of your daily life  That you had warm and trusting relationships with others  That you had experiences that challenged you to grow and become a better person  Confident to think or express your own ideas and opinions  That your life has a sense of direction or meaning to it  HADS OVERALL  HADS-A AVERAGE  HADS-D AVERAGE  I feel tense or 'wound up'  I still enjoy the things I used to enjoy  I get a sort of frightened feeling as if something awful is about to happen  I can laugh and see the funny side of things  Worrying thoughts go through my mind  I feel cheerful  I can sit at ease and feel relaxed  I feel as if I am slowed down  I get a sort of frightened feeling like 'butterflies' in my stomach  I have lost interest in my appearance  I feel restless as I have to be on the move  I look forward with enjoyment to things  I get sudden feelings of panic  I can enjoy a good book or radio or TV programme  RES_TOTAL  I tend to bounce back quickly after hard times  I have a hard time making it through stressful events*  It does not take me long to recover from a stressful event  It is hard for me to snap back when something bad happens*  I usually come through difficult times with little trouble  I tend to take a long time to get over setbacks in my life*  LONE_ TOTAL  LONE_ Emotional  LONE_ Social  I experience a general sense of emptiness  I miss having people around  There are many people I can trust completely*  I often feel rejected  There are enough people I feel close to*  There are plenty of people I can rely on when I have problems*
count       753.00                   753.00       518.00           518.00                        518.00                              518.00                           518.00       518.00                                       518.00                                             518.00                        518.00                                            518.00                                             518.00                                354.00                      354.00                 354.00                  354.00          753.00               753.00  688.00               688.0     688.00            753.00                                             688.00                                                     688.00                                                                        688.00                                        688.00                                             688.00                   753.00                                         688.00                                             688.00                                                    688.00                                                    688.00                                                                           688.00                                                     688.00               753.00          753.00          753.00                      671.00                                    671.00                         

### Numeric Summaries - Central Tendency Measures (Numerical)
We have generated the mean, median, and mode for all numeric features.

In [52]:
for column in numeric_columns_all:
    # Calculate Mean, Median, and Mode for each feature
    mean = data[column].mean()
    median = data[column].median()
    mode = data[column].mode().values[0]

    # Print the central tendency measures
    print(f"{column}:")
    print(f"Mean: {mean}")
    print(f"Median: {median}")
    print(f"Mode: {mode}")
    print("\n")


Hours sleep:
Mean: 7.148738379814077
Median: 7.0
Mode: 7.0


Weeks Social Distancing:
Mean: 4.763612217795485
Median: 5.0
Mode: 5


AIMS_ TOTAL:
Mean: 4.963706563706563
Median: 5.14
Mode: 5.14


Social Identity:
Mean: 5.094594594594595
Median: 5.33
Mode: 6.33


I consider myself an athlete:
Mean: 5.121621621621622
Median: 6.0
Mode: 6.0


I have many goals related to sport:
Mean: 5.527027027027027
Median: 6.0
Mode: 6.0


most of my friends are athletes:
Mean: 4.635135135135135
Median: 5.0
Mode: 5.0


Exclusivity:
Mean: 4.575289575289576
Median: 5.0
Mode: 5.0


Sport is the most important part of my life:
Mean: 4.718146718146718
Median: 5.0
Mode: 5.0


I spend more time thinking about sport than anything else:
Mean: 4.4324324324324325
Median: 5.0
Mode: 5.0


Negative Affectivity:
Mean: 5.155405405405405
Median: 5.5
Mode: 6.0


I feel bad about myself when I do badly in sport:
Mean: 5.063706563706564
Median: 5.0
Mode: 5.0


I would be very depressed if I were injured and could not compete

### Numeric Summaries - Box Plots (Numerical)
There are a tremendous amount of numeric features, here we are focusing specifically on the 8 numerical features ones we think would be of most importance to this project.

In [42]:
box_plots = []

for column in numeric_columns:
    box_plot = alt.Chart(data).mark_boxplot().encode(
        y=alt.Y(f'{column}:Q', title=column)
    ).properties(
        title=f'{column}',
        width = 60
    )
    box_plots.append(box_plot)

# Concatenate the individual box plots into a single row
combined_box_plots = alt.hconcat(*box_plots)

combined_box_plots

alt.HConcatChart(...)

### Visual Summaries - Histograms (Numerical)
There are a tremendous amount of numeric features, again, we are focusing specifically on the 8 numerical features ones we think would be of most importance to this project.

In [29]:
# Create histograms for each numeric column
histograms = []

for i, column in enumerate(numeric_columns):
    histogram = alt.Chart(data).mark_bar().encode(
        alt.X(column, bin=alt.Bin(maxbins=10), title=column),
        alt.Y('count()', title='Frequency')
    ).properties(
        width=200,
        height=150,
        title=f'{column}'
    )
    
    # Group histograms into rows of 4
    if i % 4 == 0:
        histograms.append([histogram])
    else:
        histograms[-1].append(histogram)

# Create a grid of subplots with 4 histograms per row
grid = []
for row in histograms:
    grid.append(alt.hconcat(*row))

# Combine the rows of subplots into a single Altair chart
histogram_chart = alt.vconcat(*grid)
histogram_chart


alt.VConcatChart(...)

### Save Data

Save wrangled and cleaned data to use voyager. Which we will use for the following univariate and multivariate visual summaries.

In [25]:
data.to_csv('data/my_data.csv', index=False)

###  Univariate  Summaries

In [ ]:
#TODO - add screenshots and description

### Multivaraite Summaries

In [44]:
#TODO - add screenshots and description

# PART II: Project Scope
## Introduction:
### **Athletes**, ***how does your training regime influence your mental wellbeing?***

Using the information collected from this survey, we plan to delve into how being an athlete can influence other aspects of your life. We are interested in picking apart how training hours, and mindset towards your sport can alter your mental health. Mainly, we want to know to what extent being an athlete can positively or negatively impact your daily wellbeing. 

The target audience for the visualizations we are going to create is other athletes seeking self-betterment. The goal is to communicate ways in which they can alter their training and/or mindset to positively influence other aspects of their lives. We hope to spread awareness about how training can impact your mental health both positively and negatively.

## Task Analysis:

#### Task 1)

Determine the range of hours of sleep athletes get versus the range of hours of sleep non-athletes get. Does age play into these ranges as well?

#### Task 2)

How does negative affectivity have any correlation with total weekly training hours, hours of sleep, or age group of the individual?

#### Task 3)

Are athletes who spend more time training/competing/playing better at managing other responsibilities?

#### Task 4)

How does psycological wellbeing relate to confidence for athletes and non-athletes? 

#### Task 5)

Do athletes or non-athletes cope with challenging experiences better, looking at negative affectivity, emotional wellbeing, etc. to better understanding ratings of challenging experiences.

# PART III: Visualization Ideas

TODO:

Preliminary Sketches

Write out each task and below each task, include the following

1. Three sketches (low fidelity) suited for the task

2. A critique of all three

3. Sketch (high fidelity) of the final one selected

4. How the sketch you selected adheres to theoretical principles you have been exposed to this term.


# PART IV: Next Steps

TODO:
Outline: List out the next 5 things that you plan to do as a group